In [2]:
# Import Statements


%matplotlib inline

import matplotlib.pyplot as plt
import numpy as np

from keras.datasets import mnist
from keras.layers import Dense, Flatten, Reshape, LeakyReLU
from keras.models import Sequential
from keras.optimizers import Adam



Deixarei aqui o código de exemplo do livro Gan's in action, referente ao capítulo 3 onde ele exemplifica o treinamento usando o mnist.

In [3]:
img_rows = 28
img_cols = 28
channels = 1

img_shape = (img_rows, img_cols, channels) # Input image dimensions
z_dim = 100 # Size of the noise vector, used as input to the Generator;

In [4]:
def build_generator(img_shape, z_dim):
    
    model = Sequential()
    
    model.add(Dense(128, input_dim=z_dim)) # Fully connected layer;
    model.add(LeakyReLU(alpha=0.01)) # Leaky ReLU activation;
    model.add(Dense(28 * 28 * 1, activation='tanh')) # Output layer with tanh activation;
    model.add(Reshape(img_shape)) # Reshapes the Generator output to image dimensions;
    
    return model

In [5]:
def build_discriminator(img_shape):
    
    model = Sequential()
    
    model.add(Flatten(input_shape=img_shape)) # Flatten the input image;
    model.add(Dense(128)) # Fully connected layer;
    model.add(LeakyReLU(alpha=0.01)) # Leaky ReLU activation;
    model.add(Dense(1, activation='sigmoid')) # Output layer with sigmoid activation;
    
    return model

In [6]:
def build_gan(generator, discriminator):
    
    model = Sequential()
    
    model.add(generator) # Combined Generator and Discriminator's model
    model.add(discriminator)
    
    return model


discriminator = build_discriminator(img_shape) # Building discriminators;
discriminator.compile(loss='binary_crossentropy',
                     optimizer=Adam(),
                     metrics=['accuracy']) # compiling the model;

generator = build_generator(img_shape, z_dim) # Building generators ;
discriminator.trainable = False # Keeps Discriminator's parameters constant for Generator training;

gan = build_gan(generator, discriminator) # Building a GAN;
gan.compile(loss='binary_crossentropy', optimizer=Adam()) # Compiling GAN model with fixed discriminator to train the Generator;

In [7]:
losses = []
accuracies = []
iteration_checkpoints = []

def train(interations, batch_size, sample_interval):
    
    (X_train, _), (_, _) = mnist.load_data() # Load the MNIST dataset;
    X_train = X_train / 127.5 - 1.0 # Rescales [0, 255] grayscale pixel values to [-1, 1];
    

    real = np.ones((batch_size,1)) # Labels for real images: all 1s;
    fake = np.zeros((batch_size, 1)) # Labels for fake images: all 0s;
    
    for iteration in range(iterations):
        
        idx = np.random.randint(0, X_train.shape[0], batch_size) # Gets a random batch of real images
        imgs = X_train[idx]
        
        z = np.random.normal(0, 1, (batch_size, 100)) # Generates a batch of fake images;
        gen_imgs = generator.predict(z)
        
        # train the discriminator:
        d_loss_real = discriminator.train_on_batch(imgs, real)
        d_loss_fake = discriminator.train_on_batch(gen_imgs, fake)
        d_loss, accuracy = 0.5 * np.add(d_loss_real, d_loss_fake)
        
        z = np.random.normal(0, 1, (batch_size, 100)) # Generates a batch of fake images;
        gen_imgs = generator.predict(z)
        
        g_loss = gan.train_on_batch(z, real) # Trains the Generator;
        
        if (iteration + 1) % sample_interval == 0:
            
            losses.append((d_loss, g_loss))
            accuracies.append((100.0 * accuracy))
            iteration_checkpoints.append(iteration + 1)
            
            print("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (iteration + 1, d_loss, 100.0 * accuracy, g_loss))
            
            sample_images(generator)

## Vamos ao output!

In [8]:
def sample_images(generator, image_grid_rows=4, image_grid_columns=4):
    
    z = np.random.normal(0, 1, (image_grid_rows * image_grid_columns, z_dim)) # Sample random noise;
    gen_imgs = generator.predict(z) # Generates images from random noise;
    gen_imgs = 0.5 * gen_imgs + 0.5 # Rescales image pixel values to [0, 1];
    
    fig, axs = plt.subplots(image_grid_rows,
                           image_grid_columns,
                            figsize=(4,4),
                            sharey=True,
                            sharex=True)
    
    cnt = 0
    for i in range(image_grid_rows):
        for j in range(image_grid_columns):
            axs[i, j].imshow(gen_imgs[cnt, :, :, 0], cmap='gray') # Outputs a grid of images;
            axs[i, j].axis('off')
            
            cnt += 1

In [ ]:
iterations = 200000
batch_size = 128
sample_interval = 1000

train(iterations, batch_size, sample_interval)

4/4 [==============================] - 0s 1ms/step


4/4 [==============================] - 0s 1ms/step


4/4 [==============================] - 0s 2ms/step


4/4 [==============================] - 0s 2ms/step


4/4 [==============================] - 0s 1ms/step


...

4/4 [==============================] - 0s 2ms/step


4/4 [==============================] - 0s 1ms/step


4/4 [==============================] - 0s 2ms/step


4/4 [==============================] - 0s 2ms/step
35000 [D loss: 0.434797, acc.: 82.03%] [G loss: 1.930238]
4/4 [==============================] - 0s 2ms/step


4/4 [==============================] - 0s 4ms/step


In [1]:
sample_images(generator)

NameError: name 'sample_images' is not defined

In [ ]:
losses = np.array(losses)

# Plot training losses for Discriminator and Generator
plt.figure(figsize=(15, 5))
plt.plot(iteration_checkpoints, losses.T[0], label="Discriminator loss")
plt.plot(iteration_checkpoints, losses.T[1], label="Generator loss")

plt.xticks(iteration_checkpoints, rotation=90)

plt.title("Training Loss")
plt.xlabel("Iteration")
plt.ylabel("Loss")
plt.legend()

this training take about 1 hour to be finished.